# EDA - Weather Forecast

In [1]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from statsmodels.tsa.seasonal import seasonal_decompose
from statsmodels.tsa.stattools import adfuller

- Aseguramos al hacer la importación que las fechas sean de tipo Datetime y los decimales en caso de tener comas se sustituya por puntos.

In [2]:
df = pd.read_csv('../Data/raw/open_meteo/historico_provincias_espana.csv')

In [3]:
df.head(5)

time  temperature_2m_max  temperature_2m_min  temperature_2m_mean  \
0  2013-01-01                12.3                 9.3                 10.8   
1  2013-01-02                12.4                 6.0                  9.1   
2  2013-01-03                16.1                 6.4                 10.1   
3  2013-01-04                15.2                 5.0                  9.0   
4  2013-01-05                14.2                 4.1                  8.2   

   precipitation_sum  windspeed_10m_max        date provincia  
0                1.2               19.8  2013-01-01  A Coruña  
1                0.0               20.4  2013-01-02  A Coruña  
2                0.0               17.1  2013-01-03  A Coruña  
3                0.0               11.3  2013-01-04  A Coruña  
4                0.0                9.7  2013-01-05  A Coruña

- Vemos la información general de nuestro dataset.

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 235235 entries, 0 to 235234
Data columns (total 8 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   time                 235235 non-null  object 
 1   temperature_2m_max   235182 non-null  float64
 2   temperature_2m_min   235182 non-null  float64
 3   temperature_2m_mean  235129 non-null  float64
 4   precipitation_sum    235129 non-null  float64
 5   windspeed_10m_max    235182 non-null  float64
 6   date                 235235 non-null  object 
 7   provincia            235235 non-null  object 
dtypes: float64(5), object(3)
memory usage: 14.4+ MB


- Borramos la columna *date*

In [5]:
df.drop(columns=['date'], inplace=True)

- Comprobamos los valores nulos.

In [6]:
df.isna().sum()

time                     0
temperature_2m_max      53
temperature_2m_min      53
temperature_2m_mean    106
precipitation_sum      106
windspeed_10m_max       53
provincia                0
dtype: int64

In [7]:
filas_con_nulos = df[df.isnull().any(axis=1)]
print(len(filas_con_nulos['provincia'].value_counts()))

52


In [8]:
df.dropna(inplace=True)

- Previamente vemos que hay diferentes datos en un mismo día sin tener en cuenta las horas, por lo que realizamos una agrupación de los datos por día segun la media.

In [9]:
df.shape

(235129, 7)

## Histograma

- Extraemos la lista de provincias

In [10]:
provincias = df['provincia'].unique()
print(len(provincias))

52


In [11]:
df_diario_madrid = df[df['provincia'] == 'Madrid']

In [12]:
df_diario_madrid.sort_values(by='time', ascending=True, inplace=True)

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_17832\3593503295.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_diario_madrid.sort_values(by='time', ascending=True, inplace=True)


### Temperatura media

In [13]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x = df_diario_madrid['time'],
        y = df_diario_madrid['temperature_2m_mean'],
        mode = 'lines',
        name = "MADRID"
    )
)

fig.update_layout(
    title = f"Evolución temporal de temperatura media para Madrid",
    xaxis_title = "Fecha",
    yaxis_title = "Temperatura Media (temperature_2m_mean)"
)

fig.show()

### Temperatura máxima

In [14]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x = df_diario_madrid['time'],
        y = df_diario_madrid['temperature_2m_max'],
        mode = 'lines',
        name = "MADRID"
    )
)

fig.update_layout(
    title = f"Evolución temporal de temperatura máxima para Madrid",
    xaxis_title = "Fecha",
    yaxis_title = "Temperatura Máxima (temperature_2m_max)"
)

fig.show()

### Temperatura mínima

In [15]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x = df_diario_madrid['time'],
        y = df_diario_madrid['temperature_2m_min'],
        mode = 'lines',
        name = "MADRID"
    )
)

fig.update_layout(
    title = f"Evolución temporal de temperatura mínima para Madrid",
    xaxis_title = "Fecha",
    yaxis_title = "Temperatura Mínima (temperature_2m_min)"
)

fig.show()

### Velocidad máxima *(km/h)*

In [16]:
fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x=df_diario_madrid['time'],
        y=df_diario_madrid['windspeed_10m_max'],
        name="MADRID",
        mode='lines'
    )
)

fig.update_layout(
    title = f"Evolución temporal de velocidad máxima del viento(km/h) para Madrid",
    xaxis_title = "Fecha",
    yaxis_title = "Velocidad media (windspeed_10m_max)"
)

fig.show()

### Precipitaciones *(mL)*

In [17]:
fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x=df_diario_madrid['time'],
        y=df_diario_madrid['precipitation_sum'],
        name="MADRID",
        mode='lines'
    )
)

fig.update_layout(
    title = f"Evolución temporal de precipitaciones en milímetros para Madrid",
    xaxis_title = "Fecha",
    yaxis_title = "Precipitaciones (precipitation_sum)"
)

fig.show()

## Tendencia, estacionalidad y ruido

### Temperatura media

In [18]:
decomposition_temp_mean = seasonal_decompose(df_diario_madrid['temperature_2m_mean'], model='additive', period=365)

#### 1. Tendencia

In [19]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_temp_mean.trend, mode='lines', name='Tendencia'))
fig_trend.update_layout(title="Tendencia de la Temperatura Media", xaxis_title="Fecha", yaxis_title="Temperatura media (°C)")
fig_trend.show()

#### 2. Estacionalidad

In [20]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_temp_mean.seasonal, mode='lines', name='Estacionalidad'))
fig_trend.update_layout(title="Estacionalidad de la Temperatura Media", xaxis_title="Fecha", yaxis_title="Temperatura media (°C)")
fig_trend.show()

#### 3. Ruido

In [21]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_temp_mean.resid, mode='lines', name='Ruido'))
fig_trend.update_layout(title="Ruido de la Temperatura Media", xaxis_title="Fecha", yaxis_title="Temperatura media (°C)")
fig_trend.show()

### Temperatura máxima

In [22]:
decomposition_temp_max = seasonal_decompose(df_diario_madrid['temperature_2m_max'], model='additive', period=365)

#### 1. Tendencia

In [23]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_temp_max.trend, mode='lines', name='Tendencia'))
fig_trend.update_layout(title="Tendencia de la Temperatura Máxima", xaxis_title="Fecha", yaxis_title="Temperatura máxima (°C)")
fig_trend.show()

#### 2. Estacionalidad

In [24]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_temp_max.seasonal, mode='lines', name='Estacionalidad'))
fig_trend.update_layout(title="Estacionalidad de la Temperatura Máxima", xaxis_title="Fecha", yaxis_title="Temperatura máxima (°C)")
fig_trend.show()

#### 3. Ruido

In [25]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_temp_max.resid, mode='lines', name='Ruido'))
fig_trend.update_layout(title="Ruido de la Temperatura Máxima", xaxis_title="Fecha", yaxis_title="Temperatura máxima (°C)")
fig_trend.show()

### Temperatura mínima

In [26]:
decomposition_temp_min = seasonal_decompose(df_diario_madrid['temperature_2m_min'], model='additive', period=365)

#### 1. Tendencia

In [27]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_temp_min.trend, mode='lines', name='Tendencia'))
fig_trend.update_layout(title="Tendencia de la Temperatura Mínima", xaxis_title="Fecha", yaxis_title="Temperatura mínima (°C)")
fig_trend.show()

#### 2. Estacionalidad

In [28]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_temp_min.seasonal, mode='lines', name='Estacionalidad'))
fig_trend.update_layout(title="Estacionalidad de la Temperatura Mínima", xaxis_title="Fecha", yaxis_title="Temperatura mínima (°C)")
fig_trend.show()

#### 3. Ruido

In [29]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_temp_min.resid, mode='lines', name='Ruido'))
fig_trend.update_layout(title="Ruido de la Temperatura Mínima", xaxis_title="Fecha", yaxis_title="Temperatura mínima (°C)")
fig_trend.show()

### Velocidad máxima del viento *(km/h)*

In [30]:
decomposition_wind_max = seasonal_decompose(df_diario_madrid['windspeed_10m_max'], model='additive', period=365)

#### 1. Tendencia

In [31]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_wind_max.trend, mode='lines', name='Tendencia'))
fig_trend.update_layout(title="Tendencia de la Velocidad Máxima del Viento", xaxis_title="Fecha", yaxis_title="Velocidad Máxima del Viento (km/h)")
fig_trend.show()

#### 2. Estacionalidad

In [32]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_wind_max.seasonal, mode='lines', name='Estacionalidad'))
fig_trend.update_layout(title="Estacionalidad de la Velocidad Máxima del Viento", xaxis_title="Fecha", yaxis_title="Velocidad Máxima del Viento (km/h)")
fig_trend.show()

#### 3. Ruido

In [33]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_wind_max.resid, mode='lines', name='Ruido'))
fig_trend.update_layout(title="Ruido de la Velocidad Máxima del Viento", xaxis_title="Fecha", yaxis_title="Velocidad Máxima del Viento (km/h)")
fig_trend.show()

### Precipitaciones máximas *(mL)*

In [34]:
decomposition_prep_max = seasonal_decompose(df_diario_madrid['precipitation_sum'], model='additive', period=365)

In [35]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_prep_max.trend, mode='lines', name='Tendencia'))
fig_trend.update_layout(title="Tendencia de precipitaciones máximas", xaxis_title="Fecha", yaxis_title="Precipitaciones Máximas del Viento (mL)")
fig_trend.show()

In [36]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_prep_max.seasonal, mode='lines', name='Estacionalidad'))
fig_trend.update_layout(title="Estacionalidad de precipitaciones máximas", xaxis_title="Fecha", yaxis_title="Precipitaciones Máximas del Viento (mL)")
fig_trend.show()

In [37]:
fig_trend = go.Figure()
fig_trend.add_trace(go.Scatter(x=df_diario_madrid['time'], y=decomposition_prep_max.resid, mode='lines', name='Ruido'))
fig_trend.update_layout(title="Ruido de precipitaciones máximas", xaxis_title="Fecha", yaxis_title="Ruido Máximas del Viento (mL)")
fig_trend.show()

# Estacionariedad

## Temperatura media

### Media Móvil

In [38]:
window_size = 365
df_diario_madrid['Rolling_Avg'] = df_diario_madrid['temperature_2m_mean'].rolling(window=window_size).mean()

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["temperature_2m_mean"],
    mode='lines',
    name='Serie Original',
    line=dict(color='blue', width=2),
    opacity=0.5
))

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["Rolling_Avg"],
    mode='lines',
    name=f'Media Móvil (Ventana={window_size})',
    line=dict(color='red', width=2),
    opacity=0.75
))

fig.update_layout(
    title='Serie Temporal vs Media Móvil',
    xaxis_title='Año',
    yaxis_title='Temperatura media',
    template='plotly_white'
)

fig.show()

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_17832\2003479964.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Vemos que el gráfico evidencia un comportamiento fuertemente estacional (la serie original) con una media anual (media móvil de 365 días) que no varía significativamente a lo largo del tiempo.

### Varianza

In [39]:
window_size = 30
df_diario_madrid['Rolling_var'] = df_diario_madrid['temperature_2m_mean'].rolling(window=window_size).var()

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["temperature_2m_mean"],
    mode='lines',
    name='Serie Original',
    line=dict(color='blue', width=2),
    opacity=0.5
))

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["Rolling_var"],
    mode='lines',
    name=f'Varianza (Ventana={window_size})',
    line=dict(color='red', width=2),
    opacity=0.75
))

fig.update_layout(
    title='Serie Temporal vs Varianza',
    xaxis_title='Año',
    yaxis_title='Temperatura media',
    template='plotly_white'
)

fig.show()

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_17832\353761407.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



- Al cargar los datos con un marco de **30 días**, vemos una clara estacionalidad por parte de la serie temporal. Por el otro lado vemos claramente que la varianza muestra también un patrón **cíclico** ya que hay períodos del año en que la varianza (la dispersión de los valores) aumenta, y otros en los que disminuye. Es probable que en las transiciones entre estaciones (por ejemplo, primavera u otoño) la temperatura cambie más drásticamente, **incrementando** la varianza.
- Para finalizar vemos que la línea roja no muestra un crecimiento o disminución de manera sostenida en el tiempo, sino **fluctuaciones cíclicas**. Esto sugiere que, si bien la temperatura presenta variaciones estacionales claras, la amplitud de esas fluctuaciones no está aumentando ni disminuyendo de forma drástica en el período observado.

## Temperatura máxima

### Media móvil

In [40]:
window_size = 365
df_diario_madrid['Rolling_Avg'] = df_diario_madrid['temperature_2m_max'].rolling(window=window_size).mean()

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["temperature_2m_max"],
    mode='lines',
    name='Serie Original',
    line=dict(color='blue', width=2),
    opacity=0.5
))

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["Rolling_Avg"],
    mode='lines',
    name=f'Media Móvil (Ventana={window_size})',
    line=dict(color='red', width=2),
    opacity=0.75
))

fig.update_layout(
    title='Serie Temporal vs Media Móvil',
    xaxis_title='Año',
    yaxis_title='Temperatura máxima',
    template='plotly_white'
)

fig.show()

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_17832\2576078017.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



### Varianza 

In [41]:
window_size = 30
df_diario_madrid['Rolling_var'] = df_diario_madrid['temperature_2m_max'].rolling(window=window_size).var()

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["temperature_2m_max"],
    mode='lines',
    name='Serie Original',
    line=dict(color='blue', width=2),
    opacity=0.5
))

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["Rolling_var"],
    mode='lines',
    name=f'Varianza (Ventana={window_size})',
    line=dict(color='red', width=2),
    opacity=0.75
))

fig.update_layout(
    title='Serie Temporal vs Varianza',
    xaxis_title='Año',
    yaxis_title='Temperatura máxima',
    template='plotly_white'
)

fig.show()

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_17832\204260578.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Temperatura mínima

### Media móvil

In [42]:
window_size = 365
df_diario_madrid['Rolling_Avg'] = df_diario_madrid['temperature_2m_min'].rolling(window=window_size).mean()

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["temperature_2m_min"],
    mode='lines',
    name='Serie Original',
    line=dict(color='blue', width=2),
    opacity=0.5
))

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["Rolling_Avg"],
    mode='lines',
    name=f'Media Móvil (Ventana={window_size})',
    line=dict(color='red', width=2),
    opacity=0.75
))

fig.update_layout(
    title='Serie Temporal vs Media Móvil',
    xaxis_title='Año',
    yaxis_title='Temperatura mínima',
    template='plotly_white'
)

fig.show()

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_17832\1980499487.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



### Varianza

In [43]:
window_size = 30
df_diario_madrid['Rolling_var'] = df_diario_madrid['temperature_2m_min'].rolling(window=window_size).var()

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["temperature_2m_min"],
    mode='lines',
    name='Serie Original',
    line=dict(color='blue', width=2),
    opacity=0.5
))

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["Rolling_var"],
    mode='lines',
    name=f'Varianza (Ventana={window_size})',
    line=dict(color='red', width=2),
    opacity=0.75
))

fig.update_layout(
    title='Serie Temporal vs Varianza',
    xaxis_title='Año',
    yaxis_title='Temperatura mínima',
    template='plotly_white'
)

fig.show()

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_17832\233653362.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Precipitaciones(mL)

### Media móvil

In [44]:
window_size = 365
df_diario_madrid['Rolling_Avg'] = df_diario_madrid['precipitation_sum'].rolling(window=window_size).mean()

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["precipitation_sum"],
    mode='lines',
    name='Serie Original',
    line=dict(color='blue', width=2),
    opacity=0.5
))

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["Rolling_Avg"],
    mode='lines',
    name=f'Media Móvil (Ventana={window_size})',
    line=dict(color='red', width=2),
    opacity=0.75
))

fig.update_layout(
    title='Serie Temporal vs Media Móvil',
    xaxis_title='Año',
    yaxis_title='Suma de precipitaciones (mL)',
    template='plotly_white'
)

fig.show()

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_17832\3647538044.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



### Varianza

In [45]:
window_size = 30
df_diario_madrid['Rolling_var'] = df_diario_madrid['precipitation_sum'].rolling(window=window_size).var()

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["precipitation_sum"],
    mode='lines',
    name='Serie Original',
    line=dict(color='blue', width=2),
    opacity=0.5
))

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["Rolling_var"],
    mode='lines',
    name=f'Varianza (Ventana={window_size})',
    line=dict(color='red', width=2),
    opacity=0.75
))

fig.update_layout(
    title='Serie Temporal vs Varianza',
    xaxis_title='Año',
    yaxis_title='Suma de precipitaciones (mL)',
    template='plotly_white'
)

fig.show()

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_17832\144791325.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Velocidad máxima del viento(km/h)

### Media móvil

In [46]:
window_size = 365
df_diario_madrid['Rolling_Avg'] = df_diario_madrid['windspeed_10m_max'].rolling(window=window_size).mean()

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["windspeed_10m_max"],
    mode='lines',
    name='Serie Original',
    line=dict(color='blue', width=2),
    opacity=0.5
))

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["Rolling_Avg"],
    mode='lines',
    name=f'Media Móvil (Ventana={window_size})',
    line=dict(color='red', width=2),
    opacity=0.75
))

fig.update_layout(
    title='Serie Temporal vs Media Móvil',
    xaxis_title='Año',
    yaxis_title='Velocidad máxima del viento (km/h)',
    template='plotly_white'
)

fig.show()

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_17832\1232381125.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



### Variaza

In [47]:
window_size = 30
df_diario_madrid['Rolling_var'] = df_diario_madrid['windspeed_10m_max'].rolling(window=window_size).var()

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["windspeed_10m_max"],
    mode='lines',
    name='Serie Original',
    line=dict(color='blue', width=2),
    opacity=0.5
))

fig.add_trace(go.Scatter(
    x=df_diario_madrid["time"],
    y=df_diario_madrid["Rolling_var"],
    mode='lines',
    name=f'Varianza (Ventana={window_size})',
    line=dict(color='red', width=2),
    opacity=0.75
))

fig.update_layout(
    title='Serie Temporal vs Varianza',
    xaxis_title='Año',
    yaxis_title='Velocidad máxima del viento (km/h)',
    template='plotly_white'
)

fig.show()

C:\Users\a.escuredo\AppData\Local\Temp\ipykernel_17832\1333589269.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Prueba de Dickey-Fuller Aumentada (ADF)

In [48]:
def check_stationarity(series, name):
    result = adfuller(series)
    print(f'ADF Statistic for {name}:', result[0])
    print('p-value:', result[1])
    if result[1] <= 0.05:
        print("The series is likely stationary.")
    else:
        print("The series is likely non-stationary.")

In [49]:
check_stationarity(df_diario_madrid['temperature_2m_mean'], 'Media de temperaturas diarias')

ADF Statistic for Media de temperaturas diarias: -4.373855802406846
p-value: 0.0003301044357165251
The series is likely stationary.


In [50]:
check_stationarity(df_diario_madrid['temperature_2m_max'], 'Máxima de temperaturas diarias')

ADF Statistic for Máxima de temperaturas diarias: -4.11910555723298
p-value: 0.0009004448694878052
The series is likely stationary.


In [51]:
check_stationarity(df_diario_madrid['temperature_2m_min'], 'Mínimo de temperaturas diarias')

ADF Statistic for Mínimo de temperaturas diarias: -4.395182706234617
p-value: 0.00030271409254623683
The series is likely stationary.


In [52]:
check_stationarity(df_diario_madrid['windspeed_10m_max'], 'Velocidad máxima del viento')

ADF Statistic for Velocidad máxima del viento: -7.2331046221210675
p-value: 1.9710853993370966e-10
The series is likely stationary.


In [53]:
check_stationarity(df_diario_madrid['precipitation_sum'], 'Precipitaciones máximas')

ADF Statistic for Precipitaciones máximas: -27.824324692960296
p-value: 0.0
The series is likely stationary.
